In [45]:
from py2neo import Graph, Node, Relationship, NodeMatcher

URL = "neo4j://localhost:7687"
AUTH = ("neo4j", "neo4j123456")
graph = Graph(URL, auth=AUTH, name='neo4j')
matcher = NodeMatcher(graph)

In [28]:
cql = "MATCH (n)-[r]-(m) return id(n) as nid,labels(n)[0] as nlabel,n.name as nname,id(r) as rid,r.name as rname,r.summary as rsummary,id(m) as mid,labels(m)[0] as mlabel,m.name as mname"


In [29]:
result = graph.run(cql)

In [30]:
data = result.data()

In [31]:
len(data)

32598

In [32]:
import json
with open('data/relation_data.json','w',encoding='utf-8') as f:
    json.dump(data,f,ensure_ascii=False,indent=4)

In [36]:
from ollama import chat
model = 'llama3.1:8b'

In [40]:
def get_answer(question,role_pros,model='llama3.1:8b'):
    messages = [
        {"role": "user", "content": role_pros},
        {"role": "user", "content": question}
    ]
    response = chat(model=model, messages=messages)
    answer = response['message']['content']
    return answer

In [39]:
role_pros="""
Please act as an expert in knowledge graphs and text analysis. Based on the input head node, tail node, and the relationship between the nodes, analyze the content of the relationship between the nodes. Simplify the relationship to no more than 5 words where applicable, and return the simplified relationship in plain text format without any additional structure or formatting.
"""

In [ ]:
len_data = len(data)-1
for index,row in enumerate(data):
    print(f"{index}/{len_data}")
    question = f"""
    My input is as follows:
Head node:{row['nname']}
Tail node:{row['mname']}
Relationship between nodes:{row['rname']}
Please return only the simplified relationship in plain text format, without any other text or punctuation.
    """
    answer = get_answer(question,role_pros,model)
    print('---------------------')
    print(row['rname'])
    print('********************')
    print(answer)
    print('---------------------')
    data[index]['simplerel']= answer

import json
with open('data/relation_data_with_simple.json','w',encoding='utf-8') as f:
    json.dump(data,f,ensure_ascii=False,indent=4)

In [46]:
import json
with open('data/relation_data_with_simple.json','r',encoding='utf-8') as f:
    data = json.load(f)

In [47]:
data[0]

{'nid': 0,
 'nlabel': 'Person',
 'nname': 'Mr. Dursley',
 'rid': 0,
 'rname': 'Mr. Dursley is afraid that someone will discover a secret about Mrs. Potter.',
 'rsummary': "The Dursleys, a seemingly ordinary family, live in Privet Drive with their son Dudley. They have a secret: they're related to the unconventional Potters, and fear that someone will discover this connection, which they consider unbecoming of themselves.",
 'mid': 1,
 'mlabel': 'Person',
 'mname': 'Mrs. Potter',
 'simplerel': 'Afraid of her secrecy'}

In [57]:
for index,row in enumerate(data):
    print(f"{index}/{len(data)}")
    simplerel = row['simplerel'].replace('"','')
    print(simplerel)
    cql = f"""
    match (n)-[r]->(m) where id(r)={row['rid']} set r.sname = "{simplerel}"
"""
    print(cql)
    graph.run(cql)
    print('---------------------')
print('关系更新完成')

0/32598
Afraid of her secrecy

    match (n)-[r]->(m) where id(r)=0 set r.sname = "Afraid of her secrecy"

---------------------
1/32598
Afraid of Harry's secrets

    match (n)-[r]->(m) where id(r)=0 set r.sname = "Afraid of Harry's secrets"

---------------------
2/32598
Accompanied the Order

    match (n)-[r]->(m) where id(r)=1 set r.sname = "Accompanied the Order"

---------------------
3/32598
Protective escort

    match (n)-[r]->(m) where id(r)=1 set r.sname = "Protective escort"

---------------------
4/32598
Director of drill manufacturer

    match (n)-[r]->(m) where id(r)=2 set r.sname = "Director of drill manufacturer"

---------------------
5/32598
Works as drill maker

    match (n)-[r]->(m) where id(r)=2 set r.sname = "Works as drill maker"

---------------------
6/32598
Spies on neighbors through fence

    match (n)-[r]->(m) where id(r)=3 set r.sname = "Spies on neighbors through fence"

---------------------
7/32598
spies on neighbors

    match (n)-[r]->(m) where id

In [58]:
#删除指向自己的关系
cql="MATCH (p)-[r]->(p) DELETE r;"
graph.run(cql)

(No data)